<h2><center>Starter Code for Lidar Car Detection</center></h2>

![](https://images.aicrowd.com/raw_images/challenges/banner_file/903/c5e145e1adaa2493032a.jpg)


### What we are going to Learn

  - Learning about how lidar works 
  - Using [scikit-learn](https://scikit-learn.org/stable/) for binary classification.

Note : Create a copy of the notebook and use the copy for submission. Go to File > Save a Copy in Drive to create a new copy



# Downloading Dataset

Installing `aicrowd-cli`

In [1]:
!pip install aicrowd-cli
%load_ext aicrowd.magic

     |████████████████████████████████| 51kB 1.0MB/s eta 0:00:01
     |████████████████████████████████| 174kB 1.9MB/s eta 0:00:01
     |████████████████████████████████| 61kB 10.0MB/s eta 0:00:01
     |████████████████████████████████| 71kB 9.3MB/s  eta 0:00:01
     |████████████████████████████████| 215kB 9.7MB/s eta 0:00:01
     |████████████████████████████████| 81kB 10.8MB/s eta 0:00:01
     |████████████████████████████████| 92kB 11.0MB/s eta 0:00:01
     |████████████████████████████████| 71kB 10.5MB/s eta 0:00:01
     |████████████████████████████████| 143kB 13.1MB/s eta 0:00:01
     |████████████████████████████████| 61kB 17.4MB/s eta 0:00:01
     |████████████████████████████████| 1.0MB 12.4MB/s eta 0:00:01
     |████████████████████████████████| 51kB 11.6MB/s eta 0:00:01
  Found existing installation: tqdm 4.46.1
    Uninstalling tqdm-4.46.1:
      Successfully uninstalled tqdm-4.46.1


In [2]:
%aicrowd login

Please login here: https://api.aicrowd.com/auth/UaIGhEPxAy_38vzZscsNRbxRQHWhkruUTvSryUihqtA
API Key valid
Saved API Key successfully!


In [ ]:
!rm -rf data
!mkdir data
%aicrowd ds dl -c lidar-car-detection -o data

test.npz:   0%|          | 0.00/163M [00:00<?, ?B/s]

train.npz:   0%|          | 0.00/108M [00:00<?, ?B/s]

# Importing Libraries

In [1]:
import pandas as pd
import numpy as np
from sklearn.model_selection import train_test_split
from sklearn.ensemble import RandomForestRegressor
import os
import matplotlib.pyplot as plt
import plotly.graph_objects as go
import random

/home/bulat/snap/jupyter/common/lib/python3.7/site-packages/joblib/_multiprocessing_helpers.py:45: UserWarning: [Errno 13] Permission denied.  joblib will operate in serial mode
  warnings.warn('%s.  joblib will operate in serial mode' % (e,))


# Reading the dataset

In [7]:
# Reading the training dataset
train_data = np.load("input/train.npz", allow_pickle=True)
train_data = train_data['train']

train_data.shape

(400, 2)

In [18]:
train_data[0,0].shape, train_data[0,1]

((38793, 3), 1)

### Visualizing the dataset

In this section, we will be visualizing a sample 3D lidar data

In [8]:
# Getting a random 3D lidar sample data
INDEX = random.randint(0, train_data.shape[0])

# Getting the individual x,y and z points.
x = train_data[INDEX][0][:, 0].tolist()
y = train_data[INDEX][0][:, 1].tolist()
z = train_data[INDEX][0][:, 2].tolist()

# Label for the corrosponding sample ( no. of cars )
label  = train_data[INDEX][1]

# Generating the 3D graph
fig = go.Figure(data=[go.Scatter3d(x=x, y=y, z=z,
                                   mode='markers',
                                   marker=dict(
                                   size=1,       
                                   colorscale='Viridis',
                                   opacity=0.8))])
print("No. of cars : ", label)
fig.show()

No. of cars :  2


Can you try finding cars in this 3d data ?

## Splitting the dataset

In [9]:
# Getting the 3d points and flattening the points into 1d array ( using only 100 training samples for faster teaining )
X = train_data[:100, 0]
X = [i.flatten()    for i in X]

# labels
y = train_data[:100, 1]

In [10]:
# Splitting the dataset into training and testing
X_train, X_val, y_train, y_val = train_test_split(X, y, test_size=0.2)

# Training the model

In [11]:
model = RandomForestRegressor(verbose=True, n_jobs=-1)

In [ ]:
model.fit(X_train, y_train)

[Parallel(n_jobs=-1)]: Using backend ThreadingBackend with 2 concurrent workers.
[Parallel(n_jobs=-1)]: Done  46 tasks      | elapsed:   41.8s
[Parallel(n_jobs=-1)]: Done 100 out of 100 | elapsed:  1.5min finished


RandomForestRegressor(bootstrap=True, ccp_alpha=0.0, criterion='mse',
                      max_depth=None, max_features='auto', max_leaf_nodes=None,
                      max_samples=None, min_impurity_decrease=0.0,
                      min_impurity_split=None, min_samples_leaf=1,
                      min_samples_split=2, min_weight_fraction_leaf=0.0,
                      n_estimators=100, n_jobs=-1, oob_score=False,
                      random_state=None, verbose=True, warm_start=False)

# Validation 

In [ ]:
model.score(X_val, y_val)

[Parallel(n_jobs=2)]: Using backend ThreadingBackend with 2 concurrent workers.
[Parallel(n_jobs=2)]: Done  46 tasks      | elapsed:    0.0s
[Parallel(n_jobs=2)]: Done 100 out of 100 | elapsed:    0.0s finished


0.028448863636363897

# Generating the predictions

In [ ]:
# Loading the test data

test_data = np.load("/content/data/test.npz", allow_pickle=True)
test_data = test_data['test']

test_data.shape

(601,)

In [ ]:
# flattening the points into 1d array
X_test = X = [i.flatten()    for i in test_data]

In [ ]:
# Generating the predictions
predictions = model.predict(X_test)
predictions.shape

[Parallel(n_jobs=2)]: Using backend ThreadingBackend with 2 concurrent workers.
[Parallel(n_jobs=2)]: Done  46 tasks      | elapsed:    0.0s
[Parallel(n_jobs=2)]: Done 100 out of 100 | elapsed:    0.0s finished


(601,)

In [ ]:
submission = pd.DataFrame({"label":predictions})
submission

label
0     2.14
1     3.56
2     2.25
3     3.02
4     2.28
..     ...
596   1.79
597   2.04
598   2.43
599   2.18
600   2.01

[601 rows x 1 columns]

In [ ]:
# Saving the predictions
!rm -rf assets
!mkdir assets
submission.to_csv(os.path.join("assets", "submission.csv"))

# Submitting our Predictions
**Note : Please save the notebook before submitting it (Ctrl + S)**

In [ ]:
!aicrowd notebook submit -c lidar-car-detection -a assets --no-verify

Mounting Google Drive 💾
Your Google Drive will be mounted to access the colab notebook
Go to this URL in a browser: https://accounts.google.com/o/oauth2/auth?client_id=947318989803-6bn6qk8qdgf4n4g3pfee6491hc0brc4i.apps.googleusercontent.com&redirect_uri=urn%3aietf%3awg%3aoauth%3a2.0%3aoob&scope=email%20https%3a%2f%2fwww.googleapis.com%2fauth%2fdocs.test%20https%3a%2f%2fwww.googleapis.com%2fauth%2fdrive%20https%3a%2f%2fwww.googleapis.com%2fauth%2fdrive.photos.readonly%20https%3a%2f%2fwww.googleapis.com%2fauth%2fpeopleapi.readonly%20https%3a%2f%2fwww.googleapis.com%2fauth%2fdrive.activity.readonly%20https%3a%2f%2fwww.googleapis.com%2fauth%2fexperimentsandconfigs%20https%3a%2f%2fwww.googleapis.com%2fauth%2fphotos.native&response_type=code

Enter your authorization code:
4/1AX4XfWhdK3UfTXVvL7raKdiHQ8QGpX1YJwQOZJoDT6NddhPN-_7kMyfCvyw
Mounted at /content/drive
Using notebook: /content/drive/MyDrive/Colab Notebooks/Lidar Car Prediction for submission...
Scrubbing API keys from the notebook...